In [1]:
from pathlib import Path

import pandas as pd

from datasets_common import write_dataset, train_test_split

In [2]:
dataset_dir = Path('ru')
parts_dir = dataset_dir / 'dataset_parts' 

In [3]:
dfs = []
for dataset_path in parts_dir.glob("*.csv"):
    dfs.append(pd.read_csv(dataset_path))
df = pd.concat(dfs)

In [4]:
label_name = 'category'
df = df.rename(columns={'categories': label_name})
for column in df.columns:
    def transform_cell(value):
        prefixes = ["{'translation_text': '", "{\'translation_text\': \'", "\'translation_text\':", "{'translation_text': \""]
        suffix = "\'}"
        for prefix in prefixes:
            if value.startswith(prefix):
                value = value[len(prefix):]
        if value.endswith(suffix):
            value = value[:-len(suffix)]
        return value
    df[column] = df[column].apply(transform_cell)

In [5]:
y = df[label_name]
X = df.drop(columns=label_name)

In [6]:
X_train, X_test, y_train, y_test = train_test_split(X, y)

In [7]:
train_filename = "arxiv_train.csv"
test_filename = "arxiv_test.csv"
write_dataset(dest_dir=dataset_dir, X=X_train, y=y_train, filename=train_filename, to_json=False)
write_dataset(dest_dir=dataset_dir, X=X_test, y=y_test, filename=test_filename, to_json=False)